# Image Thumbnails from Spitzer Enhanced Imaging Products

This notebook tutorial demonstrates the process of querying IRSA's Simple Image Access v2 (SIAv2) service for the Spitzer Enhanced Imaging Products (SEIP), making a cutout image (thumbnail), and displaying the cutout.

***

## Learning Goals

By the end of this tutorial, you will:

* Learn how to search the NASA Astronomical Virtual Observatory Directory web portal for a service that provides access to IRSA's Spitzer Enhanced Imaging Products (SEIP) images.
* Use the Python pyvo package to identify which of IRSA's SEIP images cover a specified coordinate.
* Download one of the identified images.
* Create and display a cutout of the downloaded image.

## Introduction

The Spitzer Enhanced Imaging Products (SEIP) include Super Mosaics combining data from multiple programs if appropriate, and a high-reliability Source List of compact objects. The SEIP include data from the four channels of IRAC (3.6, 4.5, 5.8, 8 microns) and the 24 micron channel of MIPS. More information about the SEIP can be found at:

https://irsa.ipac.caltech.edu/data/SPITZER/Enhanced/SEIP/

The [NASA/IPAC Infrared Science Archive (IRSA)](https://irsa.ipac.caltech.edu) at Caltech is the archive for SEIP images and catalogs. The SEIP images that are the subject of this tutorial are made accessible via the [International Virtual Observatory Alliance (IVOA)](https://ivoa.net) [Simple Image Access (SIA)](https://wiki.ivoa.net/internal/IVOA/SiaInterface/SIA-V2-Analysis.pdf) protocol. IRSA's SEIP SIA service is registered in the NASA Astronomical Virtual Observatory (NAVO) [Directory](https://vao.stsci.edu). Based on the registered information, the Python package [pyvo](https://pyvo.readthedocs.io) can be used to query the SEIP SIA service for a list of images that meet specified criteria, and standard Python libraries can be used to download and manipulate the images.
Other datasets at IRSA are available through other SIA services:

https://irsa.ipac.caltech.edu/docs/program_interface/api_images.html



## Imports

- *pyvo* for querying IRSA's SEIP SIA service
- *astropy.coordinates* for defining coordinates
- *astropy.nddata* for creating an image cutout
- *astropy.wcs* for interpreting the World Coordinate System header keywords of a fits file
- *astropy.units* for attaching units to numbers passed to the SIA service
- *matplotlib.pyplot* for plotting
- *astropy.utils.data* for downloading files
- *astropy.io* to manipulate FITS files

In [ ]:
import pyvo as vo
from astropy.coordinates import SkyCoord
from astropy.nddata import Cutout2D
from astropy.wcs import WCS
import astropy.units as u
import matplotlib.pyplot as plt
from astropy.utils.data import download_file
from astropy.io import fits

## Section 1 - Setup

Set images to display in the notebook

In [ ]:
%matplotlib inline

Define coordinates of a bright star

In [ ]:
ra = 314.30417
dec = 77.595559
pos = SkyCoord(ra=ra, dec=dec, unit='deg')

## Section 2 - Lookup and define a service for SEIP images

Start at STScI VAO Registry at https://vao.stsci.edu/keyword-search/

Search on "seip"

Locate the COLLECTION=spitzer_seip from the SIA2 URL https://irsa.ipac.caltech.edu/SIA?COLLECTION=spitzer_seip&

To work with pyvo 1.4, define this SIAv2 service and use the collection argument separately

In [ ]:
seip_service2= vo.dal.sia2.SIAService('https://irsa.ipac.caltech.edu/SIA')

## Section 3 - Search the service

Search for images covering within 10 arcseconds of the star

In [ ]:
im_table = seip_service2.search(pos=(pos.ra.deg, pos.dec.deg, 10*u.arcsec),
                                collection='spitzer_seip')

Display the table of images that is returned

In [ ]:
im_table.to_table()

## Section 4 - Locate and download an image of interest

Let's search the image results for a short-exposure IRAC Ch3 mosaic.

In [ ]:
for i in range(len(im_table)):
    if im_table[i].getdataurl().endswith('short.IRAC.3.mosaic.fits'):
        break
print(im_table[i].getdataurl())

Download the image and open it in Astropy

In [ ]:
fname = download_file(im_table[i].getdataurl(), cache=True)
image1 = fits.open(fname)

## Section 5 - Extract a cutout and plot it

In [ ]:
wcs = WCS(image1[0].header)

In [ ]:
cutout = Cutout2D(image1[0].data, pos, (60, 60), wcs=wcs)
wcs = cutout.wcs

In [ ]:
fig = plt.figure()

ax = fig.add_subplot(1, 1, 1, projection=wcs)
ax.imshow(cutout.data, cmap='gray_r', origin='lower', vmax = 10)
ax.scatter(ra, dec, transform=ax.get_transform('fk5'), s=500, edgecolor='red', facecolor='none')


## Exercise

Search the SEIP Source List using IRSA [Gator service](https://irsa.ipac.caltech.edu/cgi-bin/Gator/nph-scan?projshort=SPITZER), find an object of interest and repeat the steps above to extract cutouts in all four IRAC bands.

***

## About this notebook

**Author:** David Shupe, IRSA Scientist, and the IRSA Science Team

**Updated On:** 2022-02-14

**Contact:** irsasupport@ipac.caltech.edu or https://jira.ipac.caltech.edu/irsasupport

## Citations

If you use `astropy` for published research, please cite the authors. Follow these links for more information about citing `astropy`:

* [Citing `astropy`](https://www.astropy.org/acknowledging.html)

If you use SEIP data in published research,  please cite the dataset Digital Object Identifier (DOI): [10.26131/IRSA433](https://www.ipac.caltech.edu/doi/irsa/10.26131/IRSA433).